In [ ]:
"""
Please save notebooks with important results to your own folder in JupyterHub.

See README for usage instructions:
https://git.zooxlabs.com/zooxco/driving/blob/master/mined_metric/jupyter/README.md
"""
import json

import numpy as np
from mined_metric.jupyter.utils.data_access_util import get_experiment_data, chum_summary_stats

EXPERIMENT_ID = "EXPERIMENT_ID_PLACEHOLDER"

In [ ]:
# Retrieve all experiment data and metadata
exp_data = get_experiment_data(EXPERIMENT_ID)
if "exception" in exp_data:
    print("Invalid data is returned: %s" % exp_data["exception"])

In [ ]:
import argparse
import logging
from datetime import datetime
from dateutil.tz import tzutc
from google.protobuf.json_format import MessageToDict
from data.chum import chumpy
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
from vehicle.common.proto.decision_pb2 import Decision
import vehicle.common.proto.decision_debug_pb2 as decision_debug_pb2
# from vis.jupyter_notebooks.planner.hero_plotters import TrajectoryPlotter # for decision plotting tools
from data.chum import chumpy
from ipywidgets import interact, interactive

import bokeh.plotting as bp
import bokeh

from IPython.core.display import display, HTML, Javascript
display(HTML("<style>.container { width:95% !important; }</style>"))

bokeh.io.output_notebook()

PLANNER_DECISION_DEBUG = '/planner/decision/debug'
logger = logging.getLogger(__name__)

#from bokeh.plotting import figure, output_file, show

**Step 1:** Enter your chum uri and load active prediction information from the uri to `data`. 

In [ ]:
# Calculate basic Chum URI summary statistics
chum_uris = [d["chum_uri"] for d in exp_data["meta"]]
stats = chum_summary_stats(chum_uris)
print("Total number of Chum URIs: {}".format(len(chum_uris)))
print("Average duration of Chum URIs: {:.2f}s".format(stats["avg_duration_s"]))
print("Vehicles: {}".format(stats["vehicles_included"]))

def select_chum_uri(uri):
    return uri
chum_dropdown = interactive(select_chum_uri, uri=chum_uris)
chum_dropdown.children[0].layout.width = '95%'
chum_dropdown

In [ ]:
def load_active_prediction(uri):
    """
    Returns all active prediction data for all events.
    """
    chum_store, chum_range = chumpy.parseChumUri(uri)
    chum_range.topics = {PLANNER_DECISION_DEBUG}
    reader = chumpy.Reader.create(chum_store, chum_range)
    all_events = []
    for msg in reader:
        msg_parsed = decision_debug_pb2.Decision()
        try:
            msg_parsed.ParseFromString(msg.getData())
        except DecodeError as e:
            logger.warn('Encountered incompatible proto schema, run %s', run_id)
            continue
        
        if hasattr(msg_parsed, 'active_prediction'): 
            event = {
                'run_meta_id': uri,
                'timestamp': msg.message_timestamp / 1E9,
                'active_prediction': msg_parsed.active_prediction,
                'active_keys': msg_parsed.active_entity_key,
                'active_trajectories' : msg_parsed.active_entity_trajectory
            }
            all_events.append(event)
    if not all_events:
        print('Unable to read active prediction data from ' + uri)
    return all_events

uri = chum_uris[chum_dropdown.children[0].index]
data = load_active_prediction(uri)

In [ ]:
# Adds a trajectory to a plot.
def add_trajectory_to_plot(ax, traj, color):
    x = [state.x for state in traj.states]
    y = [state.y for state in traj.states]
    ax.plot(x,y, color)
    
def add_time_s_to_plot(ax, traj, color):
    t = traj.times
    s = [state.s for state in traj.states]
    ax.plot(t,s,color)

def add_time_velocity_to_plot(ax, traj, color):
    t = traj.times
    vx = [state.vx for state in traj.states]
    ax.plot(t,vx,color)
    
def add_time_acceleration_to_plot(ax, traj, color):
    t = traj.times
    a = [state.ax for state in traj.states]
    ax.plot(t,a,color)
    
def add_time_subgoal_to_plot(ax, traj, subgoals, color):
    t = traj.times
    subgoal_types = [subgoal.type for subgoal in subgoals]
    ax.plot(t,subgoal_types, color, marker='.')
    
def add_arc_s_to_plot(ax, traj, color):
    s = [state.s for state in traj.states]
    arc = [state.arc_length for state in traj.states]
    ax.plot(arc,s,color)
    
def add_arc_velocity_to_plot(ax, traj, color):
    arc = [state.arc_length for state in traj.states]
    vx = [state.vx for state in traj.states]
    ax.plot(arc,vx,color)
    
def add_arc_acceleration_to_plot(ax, traj, color):
    arc = [state.arc_length for state in traj.states]
    a = [state.ax for state in traj.states]
    ax.plot(arc,a,color)
    
def add_arc_subgoal_to_plot(ax, traj, subgoals, color):
    arc = [state.arc_length for state in traj.states]
    subgoal_types = [subgoal.type for subgoal in subgoals]
    ax.plot(arc_length,subgoal_types, color, marker='.')
    
# Load a vehicle belief.
def load_vehicle_belief(all_events, time_index, entity_id):
    all_samples = []
    active_prediction = all_events[time_index]['active_prediction']
    for active_entity in active_prediction.active_entity:
        if active_entity.vehicle and active_entity.vehicle.entity_id == entity_id:
            for sample in active_entity.vehicle.samples:
                all_samples.append(sample)
    return all_samples

# Load all active entity ids, return as a set
def load_active_entity_ids(all_events):
    entity_ids = set()
    for event in all_events:
        for active_entity in event['active_prediction'].active_entity:
            if active_entity.vehicle:
                entity_ids.add(active_entity.vehicle.entity_id)
    return sorted(entity_ids)

# Given a belief, generate a plot of all samples' rollout and reference trajectories.
def plot_belief_trajectories(belief, title='Belief Trajectories'):
    fig = plt.figure(figsize=(15,15))
#     fig.suptitle(title)
    gs = fig.add_gridspec(5,2)
    ax_traj = fig.add_subplot(gs[:2,:])
    ax_traj.set_xlabel('x [m]')
    ax_traj.set_ylabel('y [m]')
    ax_traj.set_aspect('equal', adjustable='box')
    ax_ts = fig.add_subplot(gs[2,0])
    ax_ts.set_xlabel('t [s]')
    ax_ts.set_ylabel('s [m]')
    ax_tv = fig.add_subplot(gs[3,0])
    ax_tv.set_xlabel('t [s]')
    ax_tv.set_ylabel('vx [m/s]')
    ax_ta = fig.add_subplot(gs[4,0])
    ax_ta.set_xlabel('t [s]')
    ax_ta.set_ylabel('ax [m/s^2]')
    #ax_tg = fig.add_subplot(gs[5,0])
    #ax_tg.set_xlabel('t [s]')
    #ax_tg.set_ylabel('subgoal type')
    ax_ss = fig.add_subplot(gs[2,1])
    ax_ss.set_xlabel('arc length [m]')
    ax_ss.set_ylabel('s [m]')
    ax_sv = fig.add_subplot(gs[3,1])
    ax_sv.set_xlabel('arc length [m]')
    ax_sv.set_ylabel('vx [m/s]')
    ax_sa = fig.add_subplot(gs[4,1])
    ax_sa.set_xlabel('arc length [m]')
    ax_sa.set_ylabel('ax [m/s^2]')
    #ax_sg = fig.add_subplot(gs[5,1])
    #ax_sg.set_xlabel('arc length [m]')
    #ax_sg.set_ylabel('subgoal type')
    legend_elements = [Line2D([0], [0], color='k', ls='-', label='Rollout Trajectory'), 
                       Line2D([0], [0], color='k', ls=':', label='Reference Trajectory')]
    
    colors = ['b', 'm', 'c', 'r', 'g', 'k']
    for sample, color in zip(belief, colors):
        add_trajectory_to_plot(ax_traj, sample.rollout_trajectory, color+'-')
        add_trajectory_to_plot(ax_traj, sample.reference_trajectory, color+':')
        add_time_s_to_plot(ax_ts, sample.rollout_trajectory, color+'-')
        add_time_s_to_plot(ax_ts, sample.reference_trajectory, color+':')
        add_time_velocity_to_plot(ax_tv, sample.rollout_trajectory, color+'-')
        add_time_velocity_to_plot(ax_tv, sample.reference_trajectory, color+':')
        add_time_acceleration_to_plot(ax_ta, sample.rollout_trajectory, color+'-')
        add_time_acceleration_to_plot(ax_ta, sample.reference_trajectory, color+':')
        #add_time_subgoal_to_plot(ax_tg, sample.rollout_trajectory, sample.subgoals, color+'-')
        add_arc_s_to_plot(ax_ss, sample.rollout_trajectory, color+'-')
        add_arc_s_to_plot(ax_ss, sample.reference_trajectory, color+':')
        add_arc_velocity_to_plot(ax_sv, sample.rollout_trajectory, color+'-')
        add_arc_velocity_to_plot(ax_sv, sample.reference_trajectory, color+':')
        add_arc_acceleration_to_plot(ax_sa, sample.rollout_trajectory, color+'-')
        add_arc_acceleration_to_plot(ax_sa, sample.reference_trajectory, color+':')
        #add_arc_subgoal_to_plot(ax_sg, sample.rollout_trajectory, sample.subgoals, color+'-')
        label = 'p(idx=' + str(sample.sample_key.trajectory_idx) + ') = {:.3f}'.format(sample.probability)
        legend_elements.append(Line2D([0],[0], color=color, label=label))
    fig.legend(handles=legend_elements, loc='upper center', ncol=len(legend_elements))
    return fig

# Get the event index of a given timestamp. Returns first event after the timestamp.
def timestamp_to_index(timestamp):
    for i in range(len(data)):
        if data[i]['timestamp'] > timestamp:
            return i
    return -1



**Step 2:** Set the timestep you are interested in as `t_default`. (optional)

In [ ]:
t_default = 1580749610.981
t_min = data[0]['timestamp']
t_max = data[-1]['timestamp']

def belief_plotter(entity_id=[], timestamp=t_default):
    index = timestamp_to_index(timestamp)
    belief = load_vehicle_belief(data, index, entity_id)
    fig = plot_belief_trajectories(belief)
    return fig

In [ ]:
all_timestamps = (t_min, t_max, 0.1)
all_entity_ids = load_active_entity_ids(data)
belief_plots = interactive(belief_plotter, entity_id=all_entity_ids, timestamp=all_timestamps);
slider = belief_plots.children[1]
slider.layout.width = '100%'
output = belief_plots.children[-1]
output.layout.min_height = '1000px'
output.layout.min_width = '1000px'

**Step 3:** Run the `belief_plots` cell below. Select the entity id of interest using the dropdown box. Use the scrollbar to select a timestamp. Use the left/right arrow keys to decrement/increment the slider.

In [ ]:
belief_plots